In [1]:
## Import necessary packages

%matplotlib osx 
# On Macs use osx
# For Windows use qt

import numpy as np
from numpy.random import rand
from landscapeWithOcean import LandscapeWithOcean # Import methods from inside file landscapeWithOcean.py

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm

## Copying the erosion lab and changing the topographic landscape 
After many fails, I decided to create one random landscape and change K and D and see how that would change the evolution of the landscape 

In [2]:
def AddHill(Z,NX,NY,xx,yy,r,h):

    for x in range(NX):
        for y in range(NY):
            dx = np.mod(x-xx+NX/2,NX)-NX/2; # difference i-i0 but apply p.b.c. 
            dy = np.mod(y-yy+NY/2,NY)-NY/2;
            dr = np.sqrt(dx**2+dy**2);
            if (dr<r):
                Z[x,y] += h * (np.cos(dr/r*np.pi/2.0))**2;

    return Z

In [3]:
### Define simulation grid and initial conditions

NX = 70*3 #number of rows- largura e largura 
NY = 70*3 #number of columns

d  = 7 # grid spacing in meters (is this the same as the valley spacing)
dx = d # keep dx=dy for simplicity
dy = d

LX=NX*dx
LY=NY*dy

# small random features in topography to begin erosion (maybe we can create something for it)
Z = rand(NX,NY)*0.1
location=np.linspace(0,1,20)

for i in range(len(location)):
    scalar=location[i]
    xx = scalar*NX
    yy = scalar*NY
    r  = (0.1+scalar)*NX
    h  = (0.1+scalar)*5
    Z = AddHill(Z,NX,NY,xx,yy,r,h)

#location=np.linspace(0,10,50)
#for i in range(len(location)):
#    scalar=location[i]
#    xx = scalar*NX
#    yy = scalar*NY
#    r  = (0.1+scalar)*NX/2
#    h  = (0.1+scalar)*10
#    Z = AddHill(Z,NX,NY,xx,yy,r,h)

#for i in range(5):
#    xx = rand()*NX
#    yy = rand()*NY
#    r  = (0.1+rand())*NX/2
#    h  = (0.5+rand())*10
#    Z = AddHill(Z,NX,NY,xx,yy,r,h)


#Z = initial_conditions(NX,NY)

#Z=np.zeros((NX,NY))
#Z[5:10,0:79]=100
#Z[50:20,30:60]=100

x = np.arange(NX)
y = np.arange(NY)
X,Y = np.meshgrid(y,x) #strange that y goes first !!!
ZMaxOrg = np.max(Z)
#print(ZMaxOrg)

In [4]:
### Physical Parameters
#Image one
K = 1.0e-6
D=0.05
#K = 1.0e-4 # meters^(1-2m)/yr(this is erosion rate)
#D = 0.00767 # This is diffusivity of soil m^2/yr



#uplift = 0.03/600.0
uplift=0

In [5]:
### Model parameters

# Time step
dt = d**2 / D / 8. 
#dt = d**2 / D /16. #extra small steps 
print(' dt[years] = ',dt)

#Area exponent A^m, default m=1
m=1

#gradient exponent g^n, default n=1
n=1

#erosion threshold 
theta_c = 10

 dt[years] =  122.5


In [6]:
# Total simulation time
T = 1000.0 * 625.0
#T=1000*100 to test the graphs 
# total number of iterations
n_iter = int(np.round(T/dt))
print('Number of interation: ',n_iter)

Number of interation:  5102


In [7]:
# Initialize landscape (change this as well since it no longer ocean)
ls = LandscapeWithOcean(NX,NY)

oceanLevelParameter=0.1  # what does this parameter do?
ls.ComputeOceanVolumeFromOceanLevelParameter(Z,NX,NY,oceanLevelParameter)

ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))

Minimum elevation           20.673811126435147
Maximum elevation           38.31924392950189
Beach level                 22.438354406741823
Ocean volume                3443.5627878901782
Percentage of ocean surface 9.564625850340136


In [8]:
# Set-up figure
# Set up figure

def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    plt.show()
    return fig

def update_figure():
        plt.clf()
        ax1 = fig.add_subplot(121,projection='3d')

        # use equal x-y aspect with an explicit vertical exageration
        vert_exag = 4.
        ax1.set_xlim3d(0,max(NX,NY))
        ax1.set_ylim3d(0,max(NX,NY))
        ax1.set_zlim3d(0,ZMaxOrg)

        ax1.set_title('Surface Relief')

#        surf = ax1.plot_surface(X,Y,Z, cmap = cm.terrain, rstride=1, cstride=1,
#                antialiased=False,linewidth=0)

        ZPlot = np.copy(Z)
        ZPlot[ZPlot<ls.ZBeachLevel] = ls.ZBeachLevel 
        ZPlot -= ls.ZBeachLevel
        ax1.plot_surface(X,Y,ZPlot, cmap = cm.terrain, rstride=1, cstride=1,
                antialiased=False,linewidth=0)

        ax2 = fig.add_subplot(122,aspect='equal')
        ax2.set_title('Elevation')

        #im = ax2.pcolor(Z,cmap=cm.terrain)
        im = ax2.pcolor(ZPlot,cmap=cm.coolwarm)
        cs = ax2.contour(ZPlot,6,colors='k')

        # Add a color bar which maps values to colors.
        cbar = fig.colorbar(im, shrink=0.5, aspect=5)
        # Add the contour line levels to the colorbar
        cbar.add_lines(cs)

        #plt.show()
        plt.draw()
        plt.pause(0.0001)

In [9]:
# Set up figure
    
fig = init_figure()
update_figure()
Znew = np.copy(Z)

# Set-up figure
# Set up figure
from matplotlib.animation import FFMpegWriter
metadata=dict(title='1D real time', artist='Matplotlib')
writer=FFMpegWriter(fps=15, metadata=metadata)
fig=plt.figure()

with writer.saving(fig,"schineiderrodriguescamila2.mp4",dpi=200):

    for it in range(1,n_iter+1):

        ls.calculate_collection_area(Z,NX,NY)
        ls.A *= dx*dy

        for i in range(NX):
            iL = np.mod(i-1,NX) # normally i-1 but observe p.b.c.
            iR = np.mod(i+1,NX) # normally i+1 but observe p.b.c.

            for j in range(NY):
                jD = np.mod(j-1,NY) # normally j-1 but observe p.b.c.
                jU = np.mod(j+1,NY) # normally j+1 but observe p.b.c.

                if ls.ocean[i,j]>0:
                    Psi_z  = 0;
                    Phi_z  = 0;
                else:
                    if ls.drain[i,j]>0: #this cell is a drain
                        s1 = (Z[iR,j]  - Z[iL,j] )/(2.*dx)
                        s2 = (Z[i,jU]  - Z[i,jD] )/(2.*dy)
                        s3 = (Z[iR,jD] - Z[iL,jU])/(2. * np.sqrt( dx**2 + dy**2) )
                        s4 = (Z[iR,jU] - Z[iL,jD])/(2. * np.sqrt( dx**2 + dy**2) )
                        gradient = (np.sqrt(s1**2 + s2**2) + np.sqrt(s3**2 + s4**2))/2.
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)            

                    elif ls.drainage[i,j]>0: #this cell is a drainage point (it drains a pool)

                        if (Z[i,j]>=Z[iR,j]) and ls.pool[iR,j]!=ls.drainage[i,j]: 
                            gradient = (Z[i,j]-Z[iR,j])/dx #pool is on my left, I drain to the right, use this gradiant
                        elif (Z[i,j]>=Z[iL,j]) and ls.pool[iL,j]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[iL,j])/dx
                        elif (Z[i,j]>=Z[i,jU]) and ls.pool[i,jU]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jU])/dy
                        elif (Z[i,j]>=Z[i,jD]) and ls.pool[i,jD]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jD])/dy
                        else:
                            gradient = 0.02 # ??? This does happen (maybe when two pools merge)
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)

                    else: #this cell is a pool, assume it has some mass diffusion but no erosion!
                        Psi_z = 0.

                    if (Psi_z<0):
                        Psi_z = 0. 

                    # diffusion term
                    Phi_z = D * ( (Z[iR,j] - 2.*Z[i,j] + Z[iL,j]) / dx**2 \
                                + (Z[i,jU] - 2.*Z[i,j] + Z[i,jD]) / dx**2 )

                Znew[i,j] = Z[i,j] + (Phi_z - Psi_z + uplift )*dt  

                dZdt= (Znew[i,j] - Z[i,j]) / dt
                CFL = abs(dZdt) * dt / min(dx,dy)
                if (CFL>1.0):
                    print('\nWarning: Time step of',dt,'is probably too large. Safer would be:',dt/CFL)

                if (Znew[i,j]<0.):
                    Znew[i,j] = 0. # yes, this does happen at the boundary when kept at zero

        #Znew[0,:] = 0.0 # resets front boundary to 0
        Z = np.copy(Znew)

        ls.pool_check(Z,NX,NY)

        if (np.mod(it,10)==0): 
            print(it,end='')
            update_figure()
            writer.grab_frame()
            print(' Ocean level=',ls.ZBeachLevel,' Ocean surface fraction=',100*ls.AOcean/(NX*NY));
        else:
            print('.',end='')

    update_figure()
    print(' Simulation finished.')

.........10 Ocean level= 22.437260574192226  Ocean surface fraction= 9.988662131519275
.........20 Ocean level= 22.436871653622067  Ocean surface fraction= 10.151927437641723
.........30 Ocean level= 22.43668768659713  Ocean surface fraction= 10.235827664399093
.........40 Ocean level= 22.43665891431029  Ocean surface fraction= 10.34013605442177
.........50 Ocean level= 22.436600393907263  Ocean surface fraction= 10.405895691609977
.........60 Ocean level= 22.436511953308166  Ocean surface fraction= 10.487528344671201
.........70 Ocean level= 22.436505379174726  Ocean surface fraction= 10.546485260770975
.........80 Ocean level= 22.436494199600965  Ocean surface fraction= 10.580498866213151
.........90 Ocean level= 22.436486971820077  Ocean surface fraction= 10.594104308390023
.........100 Ocean level= 22.436486971820077  Ocean surface fraction= 10.619047619047619
.........110 Ocean level= 22.436417841040132  Ocean surface fraction= 10.671201814058957
.........120 Ocean level= 22.43638